If you run into any issues or have questions/concerns about the data catalog API, usage patterns, or anything else, please do not hesistate to email them to danf@usc.edu.

Thanks,
Dan Feldman

### This notebook contains commands to browse available [CHIRPS](http://blog.chg.ucsb.edu/?m=201810) data using MINT Data Catalog API

In [1]:
# Prerequisites: python 3.6 or later
import requests
import json
import uuid
import pprint
import datetime
pp = pprint.PrettyPrinter(indent=2)

#### Boilerplate setup

In [2]:
# Data Catalog api endpoint url 
url = "https://api.mint-data-catalog.org"

In [3]:
# Step 1: Get session token to use the API
resp = requests.get(f"{url}/get_session_token").json()
print(resp)
api_key = resp['X-Api-Key']

request_headers = {
    'Content-Type': "application/json",
    'X-Api-Key': api_key
}

{'X-Api-Key': 'mint-data-catalog:189db916-29b7-48ec-bad2-c577fd000ba6:6058332b-a3db-4c21-a535-96af148e865b'}


In [4]:
# This is a convenience method to handle api responses. The main portion of the notebook starts in the the next cell
def handle_api_response(response, print_response=True):
    parsed_response = response.json()

    if print_response:
        pp.pprint(parsed_response)
    
    if response.status_code == 200:
        return parsed_response
    elif response.status_code == 400:
        raise Exception("Bad request ^")
    elif response.status_code == 403:
        msg = "Please make sure your request headers include X-Api-Key and that you are using correct url"
        raise Exception(msg)
    else:
        msg = """It seems our server encountered an error which it doesn't know how to handle yet. 
        This sometimes happens with unexpected input(s). In order to help us diagnose and resolve the issue, 
        please notify Dan Feldman (danf@usc.edu) of this error."""
    
    return parsed_response

#### Search queries

In [5]:
# 1. Search for datasets whose names that start with "CHIRPS" (or "chirps"; it's case-insensitive).
# Also, note the wildcard character '*' in the query. Without it, the query searches for exact matches.

search_query = {
    "dataset_names__in": ["CHIRPS*"]
}

resp = requests.post(f"{url}/find_datasets", 
                                        headers=request_headers,
                                        json=search_query)

# This will return a list of datasets that match the query, along with dataset's record_id, description, name, and metadata
response = handle_api_response(resp, print_response=True)

{ 'datasets': [ { 'dataset_description': 'CHIRPS-GEFS is a product that '
                                         "combines the NCEP's Global Ensemble "
                                         'Forecast System (GEFS) 16 day '
                                         'precipitation forecasts with the '
                                         'CHIRPS climatology to produce a '
                                         'CHIRPS compatible (latitude 50N - '
                                         '50S, ~0.05 degree resolution) '
                                         'dekadal forecasts. Precipitation '
                                         'forecasts are produced daily and '
                                         'accumulated for the 5, 10 and 15 day '
                                         'forecasts periods daily.',
                  'dataset_id': '0bf6215e-4ee9-4df3-b69e-ba1ca3686f03',
                  'dataset_metadata': { 'url': 'http://blog.chg.ucsb.edu/?m=201810',
      

In [6]:
names = [i['dataset_name'] for i in response['datasets']]
print('\n'.join(names))

CHIRPS-GEFS_precipitation_forecast_five_day_z-score
CHIRPS_accumulated_precipitation_second_dekad_anomaly
CHIRPS_accumulated_precipitation_third_dekad
CHIRPS_accumulated_precipitation_one_month
CHIRPS-GEFS_precipitation_forecast_fifteen_day_z-score
CHIRPS-GEFS_precipitation_forecast_five_day_anomaly
CHIRPS-GEFS_precipitation_forecast_ten_day_anomaly
CHIRPS_accumulated_precipitation_first_dekad_anomaly
CHIRPS_accumulated_precipitation_first_dekad_z-score
CHIRPS_accumulated_precipitation_third_dekad_anomaly
CHIRPS_accumulated_precipitation_third_dekad_z-score
CHIRPS-GEFS_precipitation_forecast_fifteen_day_anomaly
CHIRPS Version 2.0 Global Data
CHIRPS-GEFS_precipitation_forecast_ten_day_z-score
CHIRPS_accumulated_precipitation_first_dekad
CHIRPS-GEFS_precipitation_forecast_ten_day_data
fewschirps_fewsafrica_1-month
CHIRPS_accumulated_precipitation_one_month_anomaly
CHIRPS_accumulated_precipitation_one_month_z-score
CHIRPS-GEFS_precipitation_forecast_fifteen_day_data


In [7]:
# Suppose we are interested in "CHIRPS_accumulated_precipitation_one_month". 
# We can get it from the response object above in the following way (but you can use any other way of iterating through
# and filtering response object as it's a standard dict/list combo):

desired_dataset = next(dataset for dataset in response["datasets"] if dataset["dataset_name"] == "CHIRPS_accumulated_precipitation_one_month")
pp.pprint(desired_dataset)

{ 'dataset_description': 'Climate Hazard center InfraRed Precipitation with '
                         'Stations (CHIRPS) is a global (50° S - 50° N, 180° E '
                         '- 180° W), 0.05° resolution, 1981 to near-present '
                         'gridded precipitation time series. CHIRPS data are '
                         'produced by scientists at the University of '
                         'California, Santa Barbara (UCSB) Climate Hazard '
                         'Group (CHG) and the U.S. Geological Survey (USGS) '
                         'Earth Resources Observation and Science (EROS) '
                         'Center. See CHIRPS web page '
                         '(http://chg.ucsb.edu/data/chirps) for more '
                         'information.',
  'dataset_id': '246bfa91-0be9-4bee-bd44-4e1986ffd468',
  'dataset_metadata': { 'url': 'http://chg.ucsb.edu/data/chirps',
                        'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-q

In [11]:
# 2. Once we've chosen our dataset, we can use data catalog API to find more information about it.
# First, we need to note dataset's record_id since we'll need it to interact with other data catalog API 
# endpoints

dataset_id = desired_dataset["dataset_id"]
print(dataset_id)

246bfa91-0be9-4bee-bd44-4e1986ffd468


In [12]:
# 2.1 View dataset's variables
search_query = {
    "dataset_id": dataset_id
}

resp = requests.post(f"{url}/datasets/dataset_variables", 
                                        headers=request_headers,
                                        json=search_query)

# This will return a list of variables (along with variables' metadata) that our dataset contains
dataset_variables = handle_api_response(resp, print_response=True)


{ 'dataset': { 'dataset_id': '246bfa91-0be9-4bee-bd44-4e1986ffd468',
               'dataset_name': 'CHIRPS_accumulated_precipitation_one_month',
               'variables': [ { 'variable_id': '3c32a158-9a30-47d7-8c14-fe25eca2792e',
                                'variable_metadata': { 'data_type': 'float32',
                                                       'no_data': -9999.0,
                                                       'units': 'mm',
                                                       'value_max': 3000,
                                                       'value_min': 0},
                                'variable_name': 'CHIRPS_accumulated_precipitation_one_month'}]},
  'result': 'success'}


In [25]:
# 2.2 Search dataset's resources based on temporal and spatial coverage

# ----- WARNING -----------------------------------------------------------------------------
# Currently, there is a limit to the number of records that the API will return at once. 
# By default it's 20, but it's possible to return up to 2000 records by specifying the 
# appropriate limit. However, some datasets (like CHIRPS) contain ~100k resources, 
# which is why it's important to provide additional filtering criteria like spatial 
# and temporal coverage
# -------------------------------------------------------------------------------------------



# 2.2.1 Specifying spatial coverage as a lat/lon bounding box:
# Bounding box search parameter is a 4-element numeric array (in WGS84 coordinate system) [xmin, ymin, xmax, ymax]
# As a reminder, x is longitude, y is latitude

# For example, bounding box for Ethiopia+SNNPR+KAT (adm level 2) is
# {"xmax": 38.062137603759766, "xmin": 37.3511962890625, "ymax": 7.4791812896728525, "ymin": 7.147633552551269}
# We don't have to match those coordinates exactly as data catalog supports "within" and "intersects" geospatial queries
bounding_box = [35.0, 3.0, 49.0, 16.0]



# 2.2.2 Specifying temporal coverage as start/end times in ISO8601 format. Supported operators are: 
# gt (greater than), 
# gte (greater than or equal)
# lt (less than),
# lte (less than or equal)
#
# For example, to specify temporal coverage for the entire 2018, we will write 
start_time = "2018-01-01T00:00:00"
end_time = "2018-12-31T23:59:59"


# Together, the complete search query becomes
search_query = {
    "spatial_coverage__within": bounding_box,    
    "start_time__gte": start_time,
    "end_time__lte": end_time,
    "limit": 2000
}

resp = requests.post(f"{url}/datasets/find", 
                                        headers=request_headers,
                                        json=search_query)

response = handle_api_response(resp, print_response=True)

resources = response["resources"]

{ 'resources': [ { 'dataset_id': '1523d92a-550a-4fe6-9cef-738b40724371',
                   'dataset_metadata': { 'url': 'http://chg.ucsb.edu/data/chirps',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
                   'dataset_name': 'CHIRPS_accumulated_precipitation_second_dekad_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=chirps:chirps_africa_1-dekad-05-2018_mm_anomaly&lowerLeftXToUse=4339172.550541156&lowerLeftYToUse=1375183.3157732654&upperRightXToUse=4450844.076314698&upperRightYToUse=1533650.2038885967&wcsURLToUse=https://chc-ewx2.chc.ucsb.edu:8443/geoserver/wcs?&resolution=0.05&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326',
                   'resource_id': '00085012-5fc3-4155-a889-58b86de4d838',
                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                   

                   'resource_id': '07b13838-5eaa-49af-8cf4-abfed3df3c1b',
                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                          'height': 1,
                                                          'width': 1},
                                          'fews_id': { 'value': 'Ethiopia+Amhara+West '
                                                                'Gojam',
                                                       'zone_type': 'GAUL '
                                                                    'level 2'},
                                          'geospatial_metadata': { 'resolution': { 'latitude': { 'dimension': 'height',
                                                                                                 'units': 'degrees',
                                                                                                 'value': 0.05},
                                               

                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                          'height': 54,
                                                          'width': 71},
                                          'fews_id': { 'value': 'Ethiopia+Tigray',
                                                       'zone_type': 'GAUL '
                                                                    'level 1'},
                                          'geospatial_metadata': { 'resolution': { 'latitude': { 'dimension': 'height',
                                                                                                 'units': 'degrees',
                                                                                                 'value': 0.05},
                                                                                   'longitude': { 'dimension': 'width',
                                                                             

                 { 'dataset_id': '1523d92a-550a-4fe6-9cef-738b40724371',
                   'dataset_metadata': { 'url': 'http://chg.ucsb.edu/data/chirps',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
                   'dataset_name': 'CHIRPS_accumulated_precipitation_second_dekad_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=chirps:chirps_africa_1-dekad-08-2018_mm_anomaly&lowerLeftXToUse=4019574.8971754904&lowerLeftYToUse=951419.5566385173&upperRightXToUse=4139992.517585487&upperRightYToUse=1161008.4747788243&wcsURLToUse=https://chc-ewx2.chc.ucsb.edu:8443/geoserver/wcs?&resolution=0.05&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326',
                   'resource_id': '145097fa-e10f-441f-9c20-1c06dbb9c6d6',
                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                   

                                          'temporal_coverage': { 'end_time': '2018-06-20T23:59:59',
                                                                 'start_time': '2018-06-11T00:00:00'}},
                   'resource_name': 'CHIRPS_accumulated_precipitation_second_dekad_anomaly_Ethiopia+Afar+Zone '
                                    '2'},
                 { 'dataset_id': '1523d92a-550a-4fe6-9cef-738b40724371',
                   'dataset_metadata': { 'url': 'http://chg.ucsb.edu/data/chirps',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
                   'dataset_name': 'CHIRPS_accumulated_precipitation_second_dekad_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=chirps:chirps_africa_1-dekad-26-2018_mm_anomaly&lowerLeftXToUse=4122216.6620076136&lowerLeftYToUse=929030.1937975041&upperRightXToUse=4309441.5190893

...

                                          'temporal_coverage': { 'end_time': '2018-07-31T23:59:59',
                                                                 'start_time': '2018-07-01T00:00:00'}},
                   'resource_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly_Ethiopia+Afar+Zone '
                                    '5'},
                 { 'dataset_id': '18b822e5-3f74-4ed0-bda1-1719f786406c',
                   'dataset_metadata': { 'url': 'https://LDAS.GSFC.NASA.GOV/FLDAS',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
                   'dataset_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=fldassoilm10:fldassoilm10_africa_1-month-03-2018_mm_anomaly&lowerLeftXToUse=3925820.210831994&lowerLeftYToUse=974362.841092186&upperRightXToUse=4476780.858612489&uppe

                                          'spatial_coverage': { 'type': 'BoundingBox',
                                                                'value': { 'xmax': 42.9830207825,
                                                                           'xmin': 41.1777458191,
                                                                           'ymax': 9.7808227539,
                                                                           'ymin': 7.5191364288}},
                                          'temporal_coverage': { 'end_time': '2018-10-31T23:59:59',
                                                                 'start_time': '2018-10-01T00:00:00'}},
                   'resource_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly_Ethiopia+Oromia+East '
                                    'Harerge'},
                 { 'dataset_id': '18b822e5-3f74-4ed0-bda1-1719f786406c',
                   'dataset_metadata': { 'url': 'https://LDAS.GSFC.NASA.GOV/FLDAS',
       

                   'dataset_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=fldassoilm10:fldassoilm10_africa_1-month-03-2018_mm_anomaly&lowerLeftXToUse=4057808.2740735793&lowerLeftYToUse=1489418.766366375&upperRightXToUse=4209203.698796773&upperRightYToUse=1625473.1410181876&wcsURLToUse=https://chc-ewx2.chc.ucsb.edu:8443/geoserver/wcs?&resolution=0.1&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326',
                   'resource_id': '11908ad6-ffa5-4f85-b43f-0eb812eaf71b',
                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                          'height': 12,
                                                          'width': 13},
                                          'fews_id': { 'value': 'Ethiopia+Tigray+Western',
                                                       'zone_type': 'GAUL '
                                

                                                                'value': { 'xmax': 42.4022064209,
                                                                           'xmin': 39.9955215454,
                                                                           'ymax': 13.0906744003,
                                                                           'ymin': 10.7839050293}},
                                          'temporal_coverage': { 'end_time': '2018-11-30T23:59:59',
                                                                 'start_time': '2018-11-01T00:00:00'}},
                   'resource_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly_Ethiopia+Afar+Zone '
                                    '1'},
                 { 'dataset_id': '18b822e5-3f74-4ed0-bda1-1719f786406c',
                   'dataset_metadata': { 'url': 'https://LDAS.GSFC.NASA.GOV/FLDAS',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4

                   'dataset_metadata': { 'url': 'https://LDAS.GSFC.NASA.GOV/FLDAS',
                                         'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
                   'dataset_name': 'FLDAS_soil_moisture_0_10cm_one_month_anomaly',
                   'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=fldassoilm10:fldassoilm10_africa_1-month-12-2018_mm_anomaly&lowerLeftXToUse=4052273.8085755757&lowerLeftYToUse=685602.3431804352&upperRightXToUse=4084763.7920983457&upperRightYToUse=712929.9617100478&wcsURLToUse=https://chc-ewx2.chc.ucsb.edu:8443/geoserver/wcs?&resolution=0.1&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326',
                   'resource_id': '184d220c-ff96-485e-9b09-ba957635536d',
                   'resource_metadata': { 'dimensions': { 'bands': 1,
                                                          'height': 2,
                                                  

In [26]:
len(resources)

2000

In [27]:
# This is an example of a returned resource record. It contains dataset's record_id and metadata,
# resource's record_id, name, metadata, and data_url
resource_record = resources[0]
pp.pprint(resource_record)

{ 'dataset_id': '1523d92a-550a-4fe6-9cef-738b40724371',
  'dataset_metadata': { 'url': 'http://chg.ucsb.edu/data/chirps',
                        'usage_url': 'https://docs.google.com/document/d/1J-WtKoGr4nVrxvQTo-qk9Ce66_CSum5h4YDJMWvPBtA'},
  'dataset_name': 'CHIRPS_accumulated_precipitation_second_dekad_anomaly',
  'resource_data_url': 'https://chc-ewx2.chc.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=chirps:chirps_africa_1-dekad-05-2018_mm_anomaly&lowerLeftXToUse=4339172.550541156&lowerLeftYToUse=1375183.3157732654&upperRightXToUse=4450844.076314698&upperRightYToUse=1533650.2038885967&wcsURLToUse=https://chc-ewx2.chc.ucsb.edu:8443/geoserver/wcs?&resolution=0.05&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326',
  'resource_id': '00085012-5fc3-4155-a889-58b86de4d838',
  'resource_metadata': { 'dimensions': {'bands': 1, 'height': 29, 'width': 20},
                         'fews_id': { 'value': 'Ethiopia+Tigray+Southern',
                                      'zone_type': 'GAUL level 2'},


In [22]:
# In order to download actual data, we can get the relevant url from the "resource_data_url" field:

data_url = resource_record["resource_data_url"]

Replace server's to currently operational servers:

In [24]:
data_url = data_url.replace('https://chc-ewx2.chc.ucsb.edu','http://chg-ewxtest.chg.ucsb.edu')
data_url = data_url.replace(':8443',':8080')
print(data_url)

http://chg-ewxtest.chg.ucsb.edu/proxies/wcsProxy.php?layerNameToUse=chirps:chirps_africa_1-dekad-02-2018_mm_anomaly&lowerLeftXToUse=4156071.046485276&lowerLeftYToUse=810672.2755001988&upperRightXToUse=4244060.68229544&upperRightYToUse=884608.0598333525&wcsURLToUse=http://chg-ewxtest.chg.ucsb.edu:8080/geoserver/wcs?&resolution=0.05&srsToUse=EPSG:3857&outputSrsToUse=EPSG:4326
